URL 크롤링

In [2]:
# 센터검색 후 url 추출

import pandas as pd
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from webdriver_manager.chrome import ChromeDriverManager
import time

# 엑셀 파일 로드
df = pd.read_excel('seoul_gym.xlsx')

# 크롬 드라이버 실행
driver = webdriver.Chrome()
driver.implicitly_wait(10)

center_review_urls = []  # 센터 이름과 리뷰 URL을 저장할 리스트

for center_name in df['센터검색명']:
    try:
        # 지도 접속
        driver.get("https://www.google.co.kr/maps/")

        # 검색창에 센터 이름 입력
        search_box = WebDriverWait(driver, 10).until(
            EC.presence_of_element_located((By.CSS_SELECTOR, "input.searchboxinput xiQnY"))
            
        )
        search_box.clear()
        search_box.send_keys(center_name)
        search_box.send_keys(Keys.RETURN)
        time.sleep(3)  # 검색 결과 로딩 대기

        # 현재 URL을 가져와서 고유 ID 추출
        WebDriverWait(driver, 10).until(
            EC.url_contains("/place/"))  # URL이 /place/를 포함하면 계속 진행
        current_url = driver.current_url
        place_id = current_url.split('/place/')[1].split('?')[0] if '/place/' in current_url else None

        # 추출된 ID를 이용하여 방문자 리뷰 페이지 URL 생성
        if place_id:
            review_url = f"https://pcmap.place.naver.com/place/{place_id}/review/visitor"
            center_review_urls.append((center_name, review_url))

    except Exception as e:
        print(f"Error while processing {center_name}: {e}")
        continue

# 드라이버 종료
driver.quit()

# 추출한 데이터를 DataFrame으로 변환하고 엑셀로 저장
reviews_df = pd.DataFrame(center_review_urls, columns=['Center Name', 'Review URL'])
reviews_df.to_excel('GYM_urls.xlsx', index=False)

Error while processing 서울특별시 광진구 자양로 257 발레전문체력 능동센터: Message: unknown error: result.webdriverValue.value list is missing or empty in Runtime.callFunctionOn response
  (Session info: chrome=119.0.6045.124)
Stacktrace:
	GetHandleVerifier [0x00007FF61E448EF2+54786]
	(No symbol) [0x00007FF61E3B5612]
	(No symbol) [0x00007FF61E26A64B]
	(No symbol) [0x00007FF61E26EEC1]
	(No symbol) [0x00007FF61E27115F]
	(No symbol) [0x00007FF61E271250]
	(No symbol) [0x00007FF61E2AB424]
	(No symbol) [0x00007FF61E2AB91C]
	(No symbol) [0x00007FF61E2E6D87]
	(No symbol) [0x00007FF61E2CBEAF]
	(No symbol) [0x00007FF61E2E4D02]
	(No symbol) [0x00007FF61E2CBC43]
	(No symbol) [0x00007FF61E2A0941]
	(No symbol) [0x00007FF61E2A1B84]
	GetHandleVerifier [0x00007FF61E797F52+3524194]
	GetHandleVerifier [0x00007FF61E7ED800+3874576]
	GetHandleVerifier [0x00007FF61E7E5D7F+3843215]
	GetHandleVerifier [0x00007FF61E4E5086+694166]
	(No symbol) [0x00007FF61E3C0A88]
	(No symbol) [0x00007FF61E3BCA94]
	(No symbol) [0x00007FF61E3BCBC2]
	

리뷰 크롤링

In [ ]:
import pandas as pd
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from bs4 import BeautifulSoup
import time
import re


# 브라우저 옵션을 적용하여 드라이버 생성
options = webdriver.Chrome('chromedriver.exe') 

# Chrome 브라우저를 실행하는 WebDriver 객체를 생성합니다.
driver = webdriver.Chrome(options=options)

# csv 불러오기
df = pd.read_csv('C:\Users\asiae\team2_final\seoul_gym.xlsx', encoding='cp949')

# 센터검색명을 list로 변환
# excel 의 값 '센터검색명'을 list 로 변환
df_list = df['센터검색명'].tolist()

# 모든 데이터를 저장할 빈 리스트 생성
all_data = []


for name in df_list:
    url = 'https://kmong.com/@' + str(name[0])
    driver.get(url)
    time.sleep(3)

In [ ]:
import time
from selenium import webdriver
from bs4 import BeautifulSoup
import pandas as pd

# Chrome 브라우저 옵션을 설정합니다.
options = webdriver.ChromeOptions()
# Chrome 브라우저를 실행하는 WebDriver 객체를 생성합니다.
driver = webdriver.Chrome(options=options)

# csv 불러오기
df = pd.read_csv('디자인_name_scraped.csv', encoding='cp949')

# excel 의 값을 list 로 변환
df_list = df.values.tolist()

# 모든 데이터를 저장할 빈 리스트 생성
all_data = []

for name in df_list:
    url = 'https://kmong.com/@' + str(name[0])
    driver.get(url)
    time.sleep(3)

    # 현재 페이지의 HTML 코드를 가져옵니다.
    html = driver.page_source

    # HTML 파싱
    soup = BeautifulSoup(html, 'html.parser')

    # 이름
    name_element = soup.find('div', class_='ProfileMainSection__username')
    name_ = name_element.get_text(strip=True)

    # XPath 경로에 해당하는 요소를 찾아서 텍스트 값을 가져옵니다.
    rating_element = soup.find('span', class_='ProfileRateEvaluationSection__head-rate') 

    # 제목 요소와 태그 요소 추출
    title_elements = soup.find_all("div", class_="ProfileSectionTitle")[1:]  # 첫 번째 요소를 제외
    tag_group_elements = soup.find_all('div', class_="ProfileSkillSection__tag-group")

    # 프로필 요소 추출
    profile_elements = soup.find_all('span', class_="ProfileInformationSection__section-infomation-title")
    profile_d_elements = soup.find_all('span', class_="ProfileInformationSection__section-infomation-description")

    # 데이터를 담을 빈 딕셔너리 생성
    data = {'이름': name_}


    # 데이터 추출 및 리스트에 추가
    for title_element in title_elements:
        title = title_element.get_text(strip=True)
        
        if title == '받은 평가':
            rating =rating_element.get_text(strip=True)
            data[title] = rating
        else:
            if tag_group_elements:
                tag_group_element = tag_group_elements.pop(0)
                tag_texts = [tag.get_text(strip=True) for tag in tag_group_element.find_all('div', class_='ProfileSkillSection__tag')]

            else:
                tag_texts = []
        
            data[title] = ', '.join(tag_texts) if tag_texts else ''


    for profile_element, profile_d_element in zip(profile_elements, profile_d_elements):

        profile_text = profile_element.get_text(strip=True)
        profile_d_text = profile_d_element.get_text(strip=True)  
        
        data[profile_text] = profile_d_text


    # 모든 데이터를 저장할 리스트에 추가
    all_data.append(data)

# WebDriver 종료
driver.quit()

# 모든 데이터를 하나의 DataFrame으로 변환
all_data_df = pd.DataFrame(all_data)

# 엑셀 파일로 저장 (경로와 파일명을 적절히 설정하세요)
excel_file_path = '디자인_freelancer_profiles_final.xlsx'
all_data_df.to_excel(excel_file_path, index=False)

print(f"모든 데이터가 '{excel_file_path}' 파일로 저장되었습니다.")